# rf510_wsnamedsets
Organization and simultaneous fits: working with named parameter sets and parameter
snapshots in workspaces




**Author:** Wouter Verkerke  
<i><small>This notebook tutorial was automatically generated with <a href= "https://github.com/root-project/root/blob/master/documentation/doxygen/converttonotebook.py">ROOTBOOK-izer</a> from the macro found in the ROOT repository  on Wednesday, April 17, 2024 at 11:19 AM.</small></i>

In [1]:
%%cpp -d
#include "RooRealVar.h"
#include "RooDataSet.h"
#include "RooGaussian.h"
#include "RooChebychev.h"
#include "RooAddPdf.h"
#include "RooWorkspace.h"
#include "RooPlot.h"
#include "TCanvas.h"
#include "TAxis.h"
#include "TFile.h"
#include "TH1.h"

using namespace RooFit;

void fillWorkspace(RooWorkspace &w);

 Definition of a helper function: 

In [2]:
%%cpp -d
void fillWorkspace(RooWorkspace &w)
{
   // C r e a t e   m o d e l
   // -----------------------

   // Declare observable x
   RooRealVar x("x", "x", 0, 10);

   // Create two Gaussian PDFs g1(x,mean1,sigma) anf g2(x,mean2,sigma) and their parameters
   RooRealVar mean("mean", "mean of gaussians", 5, 0, 10);
   RooRealVar sigma1("sigma1", "width of gaussians", 0.5);
   RooRealVar sigma2("sigma2", "width of gaussians", 1);

   RooGaussian sig1("sig1", "Signal component 1", x, mean, sigma1);
   RooGaussian sig2("sig2", "Signal component 2", x, mean, sigma2);

   // Build Chebychev polynomial pdf
   RooRealVar a0("a0", "a0", 0.5, 0., 1.);
   RooRealVar a1("a1", "a1", 0.2, 0., 1.);
   RooChebychev bkg("bkg", "Background", x, RooArgSet(a0, a1));

   // Sum the signal components into a composite signal pdf
   RooRealVar sig1frac("sig1frac", "fraction of component 1 in signal", 0.8, 0., 1.);
   RooAddPdf sig("sig", "Signal", RooArgList(sig1, sig2), sig1frac);

   // Sum the composite signal and background
   RooRealVar bkgfrac("bkgfrac", "fraction of background", 0.5, 0., 1.);
   RooAddPdf model("model", "g1+g2+a", RooArgList(bkg, sig), bkgfrac);

   // Import model into pdf
   w.import(model);

   // E n c o d e   d e f i n i t i o n   o f   p a r a m e t e r s   i n   w o r k s p a c e
   // ---------------------------------------------------------------------------------------

   // Define named sets "parameters" and "observables", which list which variables should be considered
   // parameters and observables by the users convention
   //
   // Variables appearing in sets _must_ live in the workspace already, or the autoImport flag
   // of defineSet must be set to import them on the fly. Named sets contain only references
   // to the original variables, therefore the value of observables in named sets already
   // reflect their 'current' value
   std::unique_ptr<RooArgSet> params{model.getParameters(x)};
   w.defineSet("parameters", *params);
   w.defineSet("observables", x);

   // E n c o d e   r e f e r e n c e   v a l u e   f o r   p a r a m e t e r s   i n   w o r k s p a c e
   // ---------------------------------------------------------------------------------------------------

   // Define a parameter 'snapshot' in the pdf
   // Unlike a named set, a parameter snapshot stores an independent set of values for
   // a given set of variables in the workspace. The values can be stored and reloaded
   // into the workspace variable objects using the loadSnapshot() and saveSnapshot()
   // methods. A snapshot saves the value of each variable, any errors that are stored
   // with it as well as the 'Constant' flag that is used in fits to determine if a
   // parameter is kept fixed or not.

   // Do a dummy fit to a (supposedly) reference dataset here and store the results
   // of that fit into a snapshot
   std::unique_ptr<RooDataSet> refData{model.generate(x, 10000)};
   model.fitTo(*refData, PrintLevel(-1));

   // The true flag imports the values of the objects in (*params) into the workspace
   // If not set, the present values of the workspace parameters objects are stored
   w.saveSnapshot("reference_fit", *params, true);

   // Make another fit with the signal component forced to zero
   // and save those parameters too

   bkgfrac.setVal(1);
   bkgfrac.setConstant(true);
   bkgfrac.removeError();
   model.fitTo(*refData, PrintLevel(-1));

   w.saveSnapshot("reference_fit_bkgonly", *params, true);
}

Create model and dataset
-----------------------------------------------

In [3]:
RooWorkspace *w = new RooWorkspace("w");
fillWorkspace(*w);

[#0] WARNING:InputArguments -- The parameter 'sigma1' with range [-inf, inf] of the RooGaussian 'sig1' exceeds the safe range of (0, inf). Advise to limit its range.
[#0] WARNING:InputArguments -- The parameter 'sigma2' with range [-inf, inf] of the RooGaussian 'sig2' exceeds the safe range of (0, inf). Advise to limit its range.
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooAddPdf::model
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooChebychev::bkg
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::x
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::a0
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::a1
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooRealVar::bkgfrac
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooAddPdf::sig
[#1] INFO:ObjectHandling -- RooWorkspace::import(w) importing RooGaussian::sig1
[#1] INFO:ObjectHandling -- RooWorkspace

Warning in <ROOT::Math::Fitter::CalculateHessErrors>: Error when calculating Hessian


Exploit convention encoded in named set "parameters" and "observables"
to use workspace contents w/o need for introspected

In [4]:
RooAbsPdf *model = w->pdf("model");

Generate data from pdf in given observables

In [5]:
std::unique_ptr<RooDataSet> data{model->generate(*w->set("observables"), 1000)};

input_line_70:2:2: warning: 'data' shadows a declaration with the same name in the 'std' namespace; use '::data' to reference this declaration
 std::unique_ptr<RooDataSet> data{model->generate(*w->set("observables"), 1000)};
 ^


Fit model to data

In [6]:
model->fitTo(*data, PrintLevel(-1));

input_line_71:2:16: error: reference to 'data' is ambiguous
 model->fitTo(*data, PrintLevel(-1));
               ^
input_line_70:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{model->generate(*w->set("observables"), 1000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Plot fitted model and data on frame of first (only) observable

In [7]:
RooPlot *frame = ((RooRealVar *)w->set("observables")->first())->frame();
data->plotOn(frame);
model->plotOn(frame);

input_line_72:3:1: error: reference to 'data' is ambiguous
data->plotOn(frame);
^
input_line_70:2:30: note: candidate found by name lookup is 'data'
 std::unique_ptr<RooDataSet> data{model->generate(*w->set("observables"), 1000)};
                             ^
/usr/include/c++/9/bits/range_access.h:318:5: note: candidate found by name lookup is 'std::data'
    data(initializer_list<_Tp> __il) noexcept
    ^
/usr/include/c++/9/bits/range_access.h:289:5: note: candidate found by name lookup is 'std::data'
    data(_Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:299:5: note: candidate found by name lookup is 'std::data'
    data(const _Container& __cont) noexcept(noexcept(__cont.data()))
    ^
/usr/include/c++/9/bits/range_access.h:309:5: note: candidate found by name lookup is 'std::data'
    data(_Tp (&__array)[_Nm]) noexcept
    ^


Overlay plot with model with reference parameters as stored in snapshots

In [8]:
w->loadSnapshot("reference_fit");
model->plotOn(frame, LineColor(kRed));
w->loadSnapshot("reference_fit_bkgonly");
model->plotOn(frame, LineColor(kRed), LineStyle(kDashed));

input_line_73:3:32: error: cannot take the address of an rvalue of type 'EColor'
model->plotOn(frame, LineColor(kRed));
                               ^~~~
Error while creating dynamic expression for:
  model->plotOn(frame, LineColor(kRed))
input_line_73:5:32: error: cannot take the address of an rvalue of type 'EColor'
model->plotOn(frame, LineColor(kRed), LineStyle(kDashed));
                               ^~~~
Error while creating dynamic expression for:
  model->plotOn(frame, LineColor(kRed), LineStyle(kDashed))


Draw the frame on the canvas

In [9]:
new TCanvas("rf510_wsnamedsets", "rf503_wsnamedsets", 600, 600);
gPad->SetLeftMargin(0.15);
frame->GetYaxis()->SetTitleOffset(1.4);
frame->Draw();

IncrementalExecutor::executeFunction: symbol '_ZN5cling7runtime8internal9EvaluateTIvEET_PNS1_15DynamicExprInfoEPN5clang11DeclContextE' unresolved while linking [cling interface function]!
You are probably missing the definition of void cling::runtime::internal::EvaluateT<void>(cling::runtime::internal::DynamicExprInfo*, clang::DeclContext*)
Maybe you need to load the corresponding shared library?


Print workspace contents

In [10]:
w->Print();


RooWorkspace(w) w contents

variables
---------
(a0,a1,bkgfrac,mean,sig1frac,sigma1,sigma2,x)

p.d.f.s
-------
RooChebychev::bkg[ x=x coefList=(a0,a1) ] = 0.8
RooAddPdf::model[ bkgfrac * bkg + [%] * sig ] = 0.9/1
RooAddPdf::sig[ sig1frac * sig1 + [%] * sig2 ] = 1/1
RooGaussian::sig1[ x=x mean=mean sigma=sigma1 ] = 1
RooGaussian::sig2[ x=x mean=mean sigma=sigma2 ] = 1

parameter snapshots
-------------------
reference_fit = (a0=0.500613 +/- 0.023199,a1=0.160315 +/- 0.0373121,bkgfrac=0.504699 +/- 0.0113933,mean=5.01883 +/- 0.0101222,sigma1=0.5[C],sig1frac=0.8179 +/- 0.0374037,sigma2=1[C])
reference_fit_bkgonly = (a0=0.474264 +/- 0,a1=6.8252e-12 +/- 0,bkgfrac=1[C],mean=5.01883 +/- 0,sigma1=0.5[C],sig1frac=0.8179 +/- 0,sigma2=1[C])

named sets
----------
observables:(x)
parameters:(a0,a1,bkgfrac,mean,sig1frac,sigma1,sigma2)



Workspace will remain in memory after macro finishes

In [11]:
gDirectory->Add(w);

Draw all canvases 

In [12]:
%jsroot on
gROOT->GetListOfCanvases()->Draw()